In [1]:
__version__ = 1

Module 1- Importing libraries and preprocessing

In [2]:
from numpy import load,zeros,ones
from tensorflow import keras
from numpy.random import randint
from keras.initializers import RandomNormal
from keras import Model,Input
from keras.layers import Conv2D,Conv2DTranspose,LeakyReLU,Activation,Concatenate
from keras.layers import Dropout,BatchNormalization
import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
import os

In [ ]:
# X = np.zeros((17824, 256, 256, 3),dtype=np.float32)
# count = 0
# folder_path = "x//"
# for filename in os.listdir(folder_path):
#     img = cv.imread(folder_path+"//"+filename)
#     X[count] = ((img- 127.5) / 127.5)
#     count+=1
# np.save('D://X.npy',X)

In [ ]:
# y = np.zeros((17824, 256, 256, 3),dtype=np.float32)
# count = 0
# folder_path = "y//"
# for filename in os.listdir(folder_path):
#     img = cv.imread(folder_path+"//"+filename)
#     y[count] = ((img- 127.5) / 127.5)
#     count+=1
# np.save('D://y.npy',y)

In [3]:
X = np.load('X.npy')
y = np.load('y.npy')

In [4]:
def ssim(y_true, y_pred):
    y_true_tensor = tf.convert_to_tensor(y_true)
    y_pred_tensor = tf.convert_to_tensor(y_pred)
    ssim_value = tf.image.ssim(y_true_tensor, y_pred_tensor, max_val=1.0)
    return (1 - ssim_value)

Module 2- Defining Discriminator model

In [8]:
def define_discriminator(image_shape):
	# weight initialization
	init = RandomNormal(stddev=0.02)
	# source image input
	in_src_image = Input(shape=image_shape)
	# target image input
	in_target_image = Input(shape=image_shape)
	# concatenate images channel-wise
	merged = Concatenate()([in_src_image, in_target_image])
	# C64
	d = Conv2D(64, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(merged)
	d = LeakyReLU(alpha=0.2)(d)
	# C128
	d = Conv2D(128, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	# C256
	d = Conv2D(256, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	# C512
	d = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	# second last output layer
	d = Conv2D(512, (4,4), padding='same', kernel_initializer=init)(d)
	d = BatchNormalization()(d)
	d = LeakyReLU(alpha=0.2)(d)
	# patch output
	d = Conv2D(1, (4,4), padding='same', kernel_initializer=init)(d)
	patch_out = Activation('sigmoid')(d)
	# define model
	model = Model([in_src_image, in_target_image], patch_out)
	# compile model
	#opt = Adam(lr=0.0002, beta_1=0.5)
	model.compile(loss='binary_crossentropy', optimizer='adam', loss_weights=[0.5])
	return model

# generate samples and save as a plot and save the model
def save_models(step, g_model,d_model, dataset, n_samples=3):
    filename2 = 'GModels//gmodel_%06d.h5' % (step+1)
    g_model.save(filename2)
    filename2 = 'DModels//dmodel_%06d.h5' % (step+1)
    d_model.save(filename2)

Module 3- Defining encoder and decoder blocks

In [9]:
# define an encoder block

def define_encoder_block(layer_in, n_filters, batchnorm=True):
	# weight initialization
	init = RandomNormal(stddev=0.02)
	# add downsampling layer
	g = Conv2D(n_filters, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(layer_in)
	# conditionally add batch normalization
	if batchnorm:
		g = BatchNormalization()(g, training=True)
	# leaky relu activation
	g = LeakyReLU(alpha=0.2)(g)
	return g

# define a decoder block
def decoder_block(layer_in, skip_in, n_filters, dropout=True):
	# weight initialization
	init = RandomNormal(stddev=0.02)
	# add upsampling layer
	g = Conv2DTranspose(n_filters, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(layer_in)
	# add batch normalization
	g = BatchNormalization()(g, training=True)
	# conditionally add dropout
	if dropout:
		g = Dropout(0.5)(g, training=True)
	# merge with skip connection
	g = Concatenate()([g, skip_in])
	# relu activation
	g = Activation('relu')(g)
	return g


Module 4- Defining Generator model

In [10]:
# define the standalone generator model

def define_generator(image_shape=(256,256,3)):
	# weight initialization
	init = RandomNormal(stddev=0.02)
	# image input
	in_image = Input(shape=image_shape)
	# encoder model
	e1 = define_encoder_block(in_image, 64, batchnorm=False)
	e2 = define_encoder_block(e1, 128)
	e3 = define_encoder_block(e2, 256)
	e4 = define_encoder_block(e3, 512)
	e5 = define_encoder_block(e4, 512)
	e6 = define_encoder_block(e5, 512)
	e7 = define_encoder_block(e6, 512)
	# bottleneck, no batch norm and relu
	b = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(e7)
	b = Activation('relu')(b)
	# decoder model
	d1 = decoder_block(b, e7, 512)
	d2 = decoder_block(d1, e6, 512)
	d3 = decoder_block(d2, e5, 512)
	d4 = decoder_block(d3, e4, 512, dropout=False)
	d5 = decoder_block(d4, e3, 256, dropout=False)
	d6 = decoder_block(d5, e2, 128, dropout=False)
	d7 = decoder_block(d6, e1, 64, dropout=False)
	# output
	g = Conv2DTranspose(3, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d7)
	out_image = Activation('tanh')(g)
	# define model
	model = Model(in_image, out_image)
	return model


Module 5-Connecting generator and discriminator model

In [11]:
# define the combined generator and discriminator model, for updating the generator
def define_gan(g_model, d_model, image_shape):
	# make weights in the discriminator not trainable
	for layer in d_model.layers:
		if not isinstance(layer, BatchNormalization):
			layer.trainable = False
	# define the source image
	in_src = Input(shape=image_shape)
	# connect the source image to the generator input
	gen_out = g_model(in_src)
	# connect the source input and generator output to the discriminator input
	dis_out = d_model([in_src, gen_out])
	# src image as input, generated image and classification output
	model = Model(in_src, [dis_out, gen_out])
	# compile model
	#opt = Adam(lr=0.0002, beta_1=0.5)
	model.compile(loss=['binary_crossentropy', 'mae'], optimizer='adam', loss_weights=[1,100])
	return model

Module 6-Generating real and fake samples

In [12]:
# select a batch of random samples, returns images and target
def generate_real_samples(dataset, n_samples, patch_shape):
	# unpack dataset
	trainA, trainB = dataset
	# choose random instances
	ix = randint(0, trainA.shape[0], n_samples)
	# retrieve selected images
	X1, X2 = trainA[ix], trainB[ix]
	# generate 'real' class labels (1)
	y = ones((n_samples, patch_shape, patch_shape, 1))
	return [X1, X2], y

# generate a batch of images, returns images and targets
def generate_fake_samples(g_model, samples, patch_shape):
	# generate fake instance
	X = g_model.predict(samples)
	# create 'fake' class labels (0)
	y = zeros((len(X), patch_shape, patch_shape, 1))
	return X, y

Module 7-Training the data

In [13]:
# train pix2pix models
def train(d_model, g_model, gan_model, dataset, n_epochs=100, n_batch=1):
	# determine the output square shape of the discriminator
	n_patch = d_model.output_shape[1]
	# unpack dataset
	trainA, trainB = dataset
	# calculate the number of batches per training epoch
	bat_per_epo = int(len(trainA) / n_batch)
	# calculate the number of training iterations
	n_steps = bat_per_epo * n_epochs
	# manually enumerate epochs
	for i in range(n_steps):
		# select a batch of real samples
		[X_realA, X_realB], y_real = generate_real_samples(dataset, n_batch, n_patch)
		# generate a batch of fake samples
		X_fakeB, y_fake = generate_fake_samples(g_model, X_realA, n_patch)
		# update discriminator for real samples
		d_loss1 = d_model.train_on_batch([X_realA, X_realB], y_real)
		# update discriminator for generated samples
		d_loss2 = d_model.train_on_batch([X_realA, X_fakeB], y_fake)
		# update the generator
		g_loss, _, _ = gan_model.train_on_batch(X_realA, [y_real, X_realB])
		# summarize performance
		print('>%d / %d, d1[%.3f] d2[%.3f] g[%.3f]' % (i+1, n_steps, d_loss1, d_loss2, g_loss))
		# summarize model performance
		if ((i%1000 == 0) and i>10):
			save_models(i, g_model,d_model, dataset)

In [14]:
def Model_load(image_shape,gpath,dpath):
    gLname = -1
    dLname = -1
    
    for filename in os.listdir(gpath):
        if "model_" in filename:
            gLname = filename
    for filename in os.listdir(dpath):
        if "model_" in filename:
            dLname = filename
            
    if (gLname != -1) and (dLname != -1) and (gLname[6:] == dLname[6:]):
        print("Loading previous save: {} and {}".format(gLname[:-3],dLname[:-3]))
        g_model = tf.keras.models.load_model(gpath+gLname)
        d_model = tf.keras.models.load_model(dpath+dLname)
    else:
        print("Loading New Model")
        d_model = define_discriminator(image_shape)
        g_model = define_generator(image_shape)
        
    return g_model,d_model

Module 8- Model Summaries

In [15]:
g_model.summary()

NameError: name 'g_model' is not defined

In [16]:
d_model.summary()

NameError: name 'd_model' is not defined

Module 9-Testing of model

In [ ]:
# X are night time images
# y are day time images
# the order of x,y in dataset changes the order of model

dataset = [y,X]
print('Loaded', dataset[0].shape, dataset[1].shape)
# def ine input shape based on the loaded dataset
image_shape = X.shape[1:]
#Load models
g_model,d_model = Model_load(image_shape,gpath="GModels",dpath="DModels")
gan_model = define_gan(g_model, d_model, image_shape)
# train model
with tf.device('gpu'):
    train(d_model, g_model, gan_model, dataset,n_epochs=10)

Loaded (17824, 256, 256, 3) (17824, 256, 256, 3)
Loading New Model
Metal device set to: Apple M1


/Users/priyanshsrivastava/anaconda3/envs/gpu/lib/python3.10/site-packages/keras/initializers/initializers.py:120: UserWarning: The initializer RandomNormal is unseeded and being called multiple times, which will return identical values each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initalizer instance more than once.
  warnings.warn(
2023-10-23 19:47:57.120818: W tensorflow/tsl/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz
loc("mps_select"("(mpsFileLoc): /AppleInternal/Library/BuildRoots/75428952-3aa4-11ee-8b65-46d450270006/Library/Caches/com.apple.xbs/Sources/MetalPerformanceShadersGraph/mpsgraph/MetalPerformanceShadersGraph/Core/Files/MPSGraphUtilities.mm":294:0)): error: 'anec.gain_offset_control' op result #0 must be 4D/5D memref of 16-bit float or 8-bit signed integer or 8-bit unsigned integer values, but got 'memref<1x2x2x512xi1>'
loc("mps_select"("(mpsFileLoc): /A

1/1 [==============================] - 3s 3s/step


loc("mps_select"("(mpsFileLoc): /AppleInternal/Library/BuildRoots/75428952-3aa4-11ee-8b65-46d450270006/Library/Caches/com.apple.xbs/Sources/MetalPerformanceShadersGraph/mpsgraph/MetalPerformanceShadersGraph/Core/Files/MPSGraphUtilities.mm":294:0)): error: 'anec.gain_offset_control' op result #0 must be 4D/5D memref of 16-bit float or 8-bit signed integer or 8-bit unsigned integer values, but got 'memref<1x16x16x1xi1>'
loc("mps_select"("(mpsFileLoc): /AppleInternal/Library/BuildRoots/75428952-3aa4-11ee-8b65-46d450270006/Library/Caches/com.apple.xbs/Sources/MetalPerformanceShadersGraph/mpsgraph/MetalPerformanceShadersGraph/Core/Files/MPSGraphUtilities.mm":294:0)): error: 'anec.gain_offset_control' op result #0 must be 4D/5D memref of 16-bit float or 8-bit signed integer or 8-bit unsigned integer values, but got 'memref<1x16x16x1xi1>'
loc("mps_select"("(mpsFileLoc): /AppleInternal/Library/BuildRoots/75428952-3aa4-11ee-8b65-46d450270006/Library/Caches/com.apple.xbs/Sources/MetalPerformance

>1 / 178240, d1[0.349] d2[2.860] g[51.835]
1/1 [==============================] - 0s 20ms/step
>2 / 178240, d1[0.752] d2[1.608] g[53.801]
1/1 [==============================] - 0s 26ms/step
>3 / 178240, d1[0.300] d2[0.955] g[48.651]
1/1 [==============================] - 0s 16ms/step
>4 / 178240, d1[0.374] d2[0.459] g[28.136]
1/1 [==============================] - 0s 16ms/step
>5 / 178240, d1[0.578] d2[0.302] g[40.333]
1/1 [==============================] - 0s 16ms/step
>6 / 178240, d1[0.662] d2[0.233] g[37.943]
1/1 [==============================] - 0s 17ms/step
>7 / 178240, d1[0.676] d2[0.269] g[25.478]
1/1 [==============================] - 0s 19ms/step
>8 / 178240, d1[0.512] d2[0.397] g[58.901]
1/1 [==============================] - 0s 16ms/step
>9 / 178240, d1[0.418] d2[0.471] g[37.994]
1/1 [==============================] - 0s 16ms/step
>10 / 178240, d1[0.415] d2[0.443] g[35.841]
1/1 [==============================] - 0s 16ms/step
>11 / 178240, d1[0.354] d2[0.410] g[21.793]
1/1 [

...

1/1 [==============================] - 0s 16ms/step
>74428 / 178240, d1[0.379] d2[0.342] g[14.313]
1/1 [==============================] - 0s 15ms/step
>74429 / 178240, d1[0.382] d2[0.357] g[13.536]
1/1 [==============================] - 0s 15ms/step
>74430 / 178240, d1[0.301] d2[0.409] g[26.418]
1/1 [==============================] - 0s 15ms/step
>74431 / 178240, d1[0.312] d2[0.377] g[28.240]
1/1 [==============================] - 0s 16ms/step
>74432 / 178240, d1[0.384] d2[0.318] g[13.129]
1/1 [==============================] - 0s 15ms/step
>74433 / 178240, d1[0.383] d2[0.337] g[28.310]
1/1 [==============================] - 0s 15ms/step
>74434 / 178240, d1[0.333] d2[0.366] g[21.034]
1/1 [==============================] - 0s 15ms/step
>74435 / 178240, d1[0.330] d2[0.339] g[22.468]
1/1 [==============================] - 0s 15ms/step
>74436 / 178240, d1[0.337] d2[0.326] g[17.608]
1/1 [==============================] - 0s 15ms/step
>74437 / 178240, d1[0.376] d2[0.331] g[7.997]
1/1 [======

1/1 [==============================] - 0s 16ms/step
>74511 / 178240, d1[0.247] d2[0.414] g[12.206]
1/1 [==============================] - 0s 16ms/step
>74512 / 178240, d1[0.223] d2[0.420] g[13.446]
1/1 [==============================] - 0s 16ms/step
>74513 / 178240, d1[0.256] d2[0.348] g[25.151]
1/1 [==============================] - 0s 16ms/step
>74514 / 178240, d1[0.342] d2[0.332] g[23.248]
1/1 [==============================] - 0s 17ms/step
>74515 / 178240, d1[0.460] d2[0.238] g[15.160]
1/1 [==============================] - 0s 15ms/step
>74516 / 178240, d1[0.375] d2[0.384] g[9.178]
1/1 [==============================] - 0s 16ms/step
>74517 / 178240, d1[0.297] d2[0.381] g[18.893]
1/1 [==============================] - 0s 15ms/step
>74518 / 178240, d1[0.291] d2[0.352] g[24.033]
1/1 [==============================] - 0s 17ms/step
>74519 / 178240, d1[0.289] d2[0.298] g[40.672]
1/1 [==============================] - 0s 17ms/step
>74520 / 178240, d1[0.326] d2[0.286] g[11.161]
1/1 [======

1/1 [==============================] - 0s 17ms/step
>74594 / 178240, d1[0.334] d2[0.412] g[10.525]
1/1 [==============================] - 0s 15ms/step
>74595 / 178240, d1[0.292] d2[0.410] g[25.163]
1/1 [==============================] - 0s 15ms/step
>74596 / 178240, d1[0.363] d2[0.325] g[26.112]
1/1 [==============================] - 0s 15ms/step
>74597 / 178240, d1[0.335] d2[0.342] g[11.859]
1/1 [==============================] - 0s 16ms/step
>74598 / 178240, d1[0.462] d2[0.293] g[26.002]
1/1 [==============================] - 0s 17ms/step
>74599 / 178240, d1[0.323] d2[0.346] g[24.448]
1/1 [==============================] - 0s 16ms/step
>74600 / 178240, d1[0.309] d2[0.359] g[23.642]
1/1 [==============================] - 0s 15ms/step
>74601 / 178240, d1[0.301] d2[0.327] g[28.113]
1/1 [==============================] - 0s 16ms/step
>74602 / 178240, d1[0.381] d2[0.367] g[16.356]
1/1 [==============================] - 0s 15ms/step
>74603 / 178240, d1[0.292] d2[0.401] g[10.107]
1/1 [=====

1/1 [==============================] - 0s 15ms/step
>74677 / 178240, d1[0.303] d2[0.395] g[28.390]
1/1 [==============================] - 0s 16ms/step
>74678 / 178240, d1[0.250] d2[0.521] g[21.819]
1/1 [==============================] - 0s 16ms/step
>74679 / 178240, d1[0.328] d2[0.315] g[37.513]
1/1 [==============================] - 0s 16ms/step
>74680 / 178240, d1[0.285] d2[0.410] g[17.365]
1/1 [==============================] - 0s 16ms/step
>74681 / 178240, d1[0.492] d2[0.201] g[25.957]
1/1 [==============================] - 0s 16ms/step
>74682 / 178240, d1[0.309] d2[0.385] g[8.098]
1/1 [==============================] - 0s 15ms/step
>74683 / 178240, d1[0.423] d2[0.299] g[34.876]
1/1 [==============================] - 0s 16ms/step
>74684 / 178240, d1[0.262] d2[0.475] g[7.481]
1/1 [==============================] - 0s 15ms/step
>74685 / 178240, d1[0.258] d2[0.424] g[17.447]
1/1 [==============================] - 0s 15ms/step
>74686 / 178240, d1[0.295] d2[0.377] g[11.978]
1/1 [=======

1/1 [==============================] - 0s 16ms/step
>74760 / 178240, d1[0.374] d2[0.339] g[22.944]
1/1 [==============================] - 0s 15ms/step
>74761 / 178240, d1[0.354] d2[0.358] g[30.109]
1/1 [==============================] - 0s 16ms/step
>74762 / 178240, d1[0.334] d2[0.321] g[16.848]
1/1 [==============================] - 0s 16ms/step
>74763 / 178240, d1[0.344] d2[0.351] g[12.168]
1/1 [==============================] - 0s 16ms/step
>74764 / 178240, d1[0.326] d2[0.283] g[15.649]
1/1 [==============================] - 0s 17ms/step
>74765 / 178240, d1[0.325] d2[0.274] g[21.738]
1/1 [==============================] - 0s 15ms/step
>74766 / 178240, d1[0.454] d2[0.358] g[37.931]
1/1 [==============================] - 0s 15ms/step
>74767 / 178240, d1[0.271] d2[0.416] g[34.093]
1/1 [==============================] - 0s 15ms/step
>74768 / 178240, d1[0.349] d2[0.339] g[20.173]
1/1 [==============================] - 0s 16ms/step
>74769 / 178240, d1[0.276] d2[0.430] g[10.557]
1/1 [=====

In [1]:
plt.imshow(y[:10][0])

NameError: name 'plt' is not defined

In [ ]:
pred = g_model.predict(y[:10])
plt.imshow(pred[0])